# Installing dependancies

In [1]:
pip install pandas numpy scikit-learn matplotlib seaborn


[notice] A new release of pip is available: 25.0.1 -> 25.3
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


# Importing all necessary libraries

In [2]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
import matplotlib.pyplot as plt
import seaborn as sns
print("libraries imported")

libraries imported


# Load the gene expression data

In [3]:
expression_df = pd.read_csv('TCGA_PANCAN_HiSeqV2_PANCAN.gz', sep='\t', index_col=0)
print("expression data shape:",expression_df.shape)

expression data shape: (20531, 11069)


# Load the phenotype/metadata

In [4]:
phenotype_df = pd.read_csv('TCGA_PANCAN_clinical.tsv', sep='\t', index_col=0)
print("phenotype data shape:",phenotype_df.shape)

phenotype data shape: (12591, 33)


# Transposed expression data

In [5]:
tran_expression_df = expression_df.T
print("transposed expression shape:", tran_expression_df.shape)
tran_expression_df.head(1)

transposed expression shape: (11069, 20531)


sample           100130426  100133144  100134869  10357  10431  136542  \
TCGA-OR-A5J1-01        0.0       2.09        2.3   7.23  10.99     0.0   

sample           155060  26823  280660  317712  ...  ZWILCH  ZWINT  ZXDA  \
TCGA-OR-A5J1-01     8.1   1.29     0.0     0.0  ...    7.53   7.21  4.44   

sample           ZXDB   ZXDC  ZYG11A  ZYG11B    ZYX  ZZEF1  ZZZ3  
TCGA-OR-A5J1-01  8.46  10.04    0.57    9.34  10.85  10.18  9.22  

[1 rows x 20531 columns]

# Merged gene expression and phenotype data

In [6]:
merged_df = tran_expression_df.join(phenotype_df[['histological_type']])
print("Shape before dropping rows with missing values:", merged_df.shape)

Shape before dropping rows with missing values: (11069, 20532)


In [7]:
merged_df.dropna(inplace=True)
print("Shape after dropping rows with missing values:", merged_df.shape)

Shape after dropping rows with missing values: (8785, 20532)


In [8]:
y = merged_df['histological_type']
X = merged_df.drop(columns=['histological_type'])

In [9]:
print("Cleanned and aligned data")
print("Final X shape:", X.shape)
print("Final y shape:", y.shape)

Cleanned and aligned data
Final X shape: (8785, 20531)
Final y shape: (8785,)


# Feature Selection

In [10]:
gene_variance = X.var()
#print("Gene Variance:", gene_variance)

In [11]:
N_FEATURES = 5000
top_genes = gene_variance.nlargest(N_FEATURES).index
X_filtered = X[top_genes]

print(f"\nSelected the top {N_FEATURES} most variable genes.")
print(f"Filtered X shape:", X_filtered.shape)


Selected the top 5000 most variable genes.
Filtered X shape: (8785, 5000)


# Removing single-member classes

In [12]:
class_counts = y.value_counts()
print("\nClass counts before filtering single-member classes;")
print(class_counts)


Class counts before filtering single-member classes;
histological_type
Infiltrating Ductal Carcinoma                                                                                                                                     882
Kidney Clear Cell Renal Carcinoma                                                                                                                                 606
Lung Adenocarcinoma                                                                                                                                               576
Head & Neck Squamous Cell Carcinoma                                                                                                                               555
Lung Squamous Cell Carcinoma                                                                                                                                      552
                                                                                                  

In [13]:
classes_to_keep = class_counts[class_counts >= 100].index

In [14]:
is_class_to_keep = y.isin(classes_to_keep)

In [15]:
X_final = X_filtered[is_class_to_keep]
y_final = y[is_class_to_keep]

In [16]:
print("X_final shape:", X_final.shape)
print("y_final shape:", y_final.shape)

X_final shape: (7327, 5000)
y_final shape: (7327,)


# Model Training and Evaluation

In [17]:
X_train, X_test, y_train, y_test = train_test_split(X_final, y_final, test_size=0.2, random_state=42, stratify=y_final)

In [18]:
model = RandomForestClassifier(n_estimators=100, random_state=42, n_jobs=-1)
model.fit(X_train, y_train)

RandomForestClassifier(n_jobs=-1, random_state=42)

In [19]:
y_pred = model.predict(X_test)

In [20]:
accuracy = accuracy_score(y_test, y_pred)
print(f"\nModel Accuracy on Test set: {accuracy:.4f}")


Model Accuracy on Test set: 0.8997


In [21]:
print("Classification Report:")
print(classification_report(y_test, y_pred))

Classification Report:
                                                                        precision    recall  f1-score   support

                                                           Astrocytoma       0.57      0.72      0.64        39
                                      Cervical Squamous Cell Carcinoma       0.98      0.86      0.92        51
                                                  Colon Adenocarcinoma       0.98      1.00      0.99        57
                               Endometrioid endometrial adenocarcinoma       0.85      0.96      0.90        23
                                   Head & Neck Squamous Cell Carcinoma       0.96      0.97      0.97       111
                                              Hepatocellular Carcinoma       1.00      0.98      0.99        82
                                         Infiltrating Ductal Carcinoma       0.85      0.98      0.91       177
                                        Infiltrating Lobular Carcinoma       0.8

In [22]:
class_names = sorted(y_final.unique())

In [23]:
cm = confusion_matrix(y_test, y_pred, labels=class_names)

In [24]:
plt.figure(figsize=(150, 120))
sns.heatmap(cm, annot=True, fmt='d', cmap='Blues', linewidths=2, linecolor='black', xticklabels=class_names, yticklabels=class_names)
plt.title('Confusion Matrix: Predicted Cancer Types', fontsize=100)
plt.ylabel('True Label', fontsize=100)
plt.xlabel('Predicted Label', fontsize=100)
plt.xticks(rotation=45, ha='right', fontsize=70)
plt.yticks(rotation=0, fontsize=70)
plt.tight_layout()
plt.savefig("myplot.png", dpi=300, bbox_inches='tight')
plt.show()